In [1]:
import cnvpytor
import subprocess

print(cnvpytor.__version__)

1.3.1


In [2]:
filename = "test_with_del__2_formated.fa"
command = f"cat {filename} | wc -l"
result = subprocess.check_output(command, shell=True)
line_count = int(result.strip())
line_count

3697817

In [3]:
read_count = line_count * 50 * 30 / 202
read_count = round(read_count)
read_count

27459037

In [4]:
command = f"wgsim -d 300 -N {read_count} -1 101 -2 101 {filename} frag1Copy_test.fastq frag2Copy_test.fastq"
result = subprocess.check_output(command, shell=True)
print(result)

[wgsim] seed = 1707234491
[wgsim_core] calculating the total length of the reference sequence...
[wgsim_core] 1 sequences, total length: 184890774


b'chr22\t102\tT\tG\t-\nchr22\t1602\tA\tT\t-\nchr22\t2231\tT\tY\t+\nchr22\t2509\tC\tM\t+\nchr22\t4771\tA\tM\t+\nchr22\t5648\tT\tC\t-\nchr22\t6837\tT\tY\t+\nchr22\t7230\tT\tK\t+\nchr22\t7845\tC\tG\t-\nchr22\t9577\tA\tC\t-\nchr22\t9654\tG\tR\t+\nchr22\t10575\tT\tK\t+\nchr22\t11190\tA\tR\t+\nchr22\t12327\tC\tA\t-\nchr22\t13155\tC\tT\t-\nchr22\t13746\t-\tT\t+\nchr22\t14158\t-\tGA\t-\nchr22\t14859\tG\tK\t+\nchr22\t15976\tT\tA\t-\nchr22\t20914\tC\tA\t-\nchr22\t22065\tG\tT\t-\nchr22\t24817\tC\tM\t+\nchr22\t26879\tT\tY\t+\nchr22\t28008\tA\tT\t-\nchr22\t28561\tA\t-\t-\nchr22\t29077\tG\tC\t-\nchr22\t29780\tA\tT\t-\nchr22\t32584\tT\tW\t+\nchr22\t33043\tA\tC\t-\nchr22\t35135\tC\tA\t-\nchr22\t35186\tT\tC\t-\nchr22\t36369\tG\tS\t+\nchr22\t38472\tA\tR\t+\nchr22\t41951\tT\tK\t+\nchr22\t43233\tC\tY\t+\nchr22\t43815\tC\tT\t-\nchr22\t45570\tC\tM\t+\nchr22\t51451\tC\tA\t-\nchr22\t51716\tA\tR\t+\nchr22\t51845\tT\tC\t-\nchr22\t52365\tA\tC\t-\nchr22\t52575\t-\tC\t+\nchr22\t54666\tC\tG\t-\nchr22\t55084\tG\tK\t

In [5]:
# bowtie related stuff
!bowtie2-build reference.fa bias
!bowtie2 -p 4 -k 15 --no-mixed -x bias -1 frag1Copy_test.fastq -2 frag2Copy_test.fastq -S biasOut.sam

Settings:
  Output files: "bias.*.bt2"
  Line rate: 6 (line is 64 bytes)
  Lines per side: 1 (side is 64 bytes)
  Offset rate: 4 (one in 16)
  FTable chars: 10
  Strings: unpacked
  Max bucket size: default
  Max bucket size, sqrt multiplier: default
  Max bucket size, len divisor: 4
  Difference-cover sample period: 1024
  Endianness: little
  Actual local endianness: little
  Sanity checking: disabled
  Assertions: disabled
  Random seed: 0
  Sizeofs: void*:8, int:4, long:8, size_t:8
Input files DNA, FASTA:
  reference.fa
Building a SMALL index
Reading reference sizes
  Time reading reference sizes: 00:00:01
Calculating joined length
Writing header
Reserving space for joined string
Joining reference sequences
  Time to join reference sequences: 00:00:00
bmax according to bmaxDivN setting: 12826141
Using parameters --bmax 9619606 --dcv 1024
  Doing ahead-of-time memory usage test
  Passed!  Constructing with these parameters: --bmax 9619606 --dcv 1024
Constructing suffix-array element

In [7]:
# sam to bam file conversion
!samtools sort biasOut.sam -o biasOut_sorted.bam
!samtools index biasOut_sorted.bam

In [8]:
app = cnvpytor.Root("test.pytor", create=True, max_cores=8)

In [9]:
app.rd(["biasOut_sorted.bam"])

In [10]:
app.calculate_histograms([100, 1000, 10000, 100000, 1000000, 10000000])

In [11]:
app.partition([100, 1000, 10000, 100000, 1000000, 10000000])

In [12]:
calls = app.call([100, 1000, 10000, 100000, 1000000, 10000000], print_calls=True)

deletion	chr22:1-16050100	16050100	0.0000	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0000	1.0000	0
deletion	chr22:16697801-16847900	150100	0.0002	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0000	0.9993	0
deletion	chr22:20509401-20609500	100100	0.0004	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0154	0.9990	0
deletion	chr22:37617601-51304600	13687000	0.5953	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0002	0.0080	0
deletion	chr22:1-16050000	16050000	0.0000	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	-1.0000	1.0000	0
deletion	chr22:16698001-16848000	150000	0.0005	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0000	0.9990	0
deletion	chr22:20509001-20610000	101000	0.0086	0.000000e+00	3.311069e-94	0.000000e+00	5.744647e-243	0.0015	0.9901	0
deletion	chr22:37617001-51305000	13688000	0.6007	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0002	0.0081	0
deletion	chr22:1-16050000	16050000	0.0000	0.000000e+00	0.000000e+00	0.000000e+00	0.0

In [13]:
for bin_size in calls:
    print("Bin size: ", bin_size)

Bin size:  100
Bin size:  1000
Bin size:  10000
Bin size:  100000
Bin size:  1000000
Bin size:  10000000


In [14]:
print(f"{filename=}, Histogram Size: 100")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[100]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 100
type,chromosome_name,start,end,size,cnv_level,q0
deletion,chr22,1,16050100,16050100,3.0390904519100183e-06,0.0
deletion,chr22,16697801,16847900,150100,0.00020403584113628357,0.0
deletion,chr22,20509401,20609500,100100,0.00043247277900845333,0.015384615384615385
deletion,chr22,37617601,51304600,13687000,0.5953376767584561,0.0001625780962919477


In [15]:
print(f"{filename=}, Histogram Size: 1000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[1000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 1000
type,chromosome_name,start,end,size,cnv_level,q0
deletion,chr22,1,16050000,16050000,0.0,-1
deletion,chr22,16698001,16848000,150000,0.000469628578375242,0.0
deletion,chr22,20509001,20610000,101000,0.008550871533995164,0.001486988847583643
deletion,chr22,37617001,51305000,13688000,0.6006768181406271,0.0001625640708968841


In [16]:
print(f"{filename=}, Histogram Size: 10,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[10000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 10,000
type,chromosome_name,start,end,size,cnv_level,q0
deletion,chr22,1,16050000,16050000,0.0,-1
deletion,chr22,16700001,16850000,150000,0.015326040077212874,0.0
deletion,chr22,20510001,20610000,100000,0.005315477351138403,0.002472187886279357
deletion,chr22,37620001,51310000,13690000,0.6246900671683357,0.00016260542438727225


In [17]:
print(f"{filename=}, Histogram Size: 100,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[100000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 100,000
type,chromosome_name,start,end,size,cnv_level,q0
deletion,chr22,1,16000000,16000000,0.0,-1
deletion,chr22,37800001,51400000,13600000,0.6478575915876452,0.00016394785076667947


In [18]:
print(f"{filename=}, Histogram Size: 1,000,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[1000000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 1,000,000
type,chromosome_name,start,end,size,cnv_level,q0
deletion,chr22,1,16000000,16000000,0.0,-1


In [19]:
print(f"{filename=}, Histogram Size: 10,000,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[10000000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__2_formated.fa', Histogram Size: 10,000,000
type,chromosome_name,start,end,size,cnv_level,q0


In [20]:
del app